<a href="https://colab.research.google.com/gist/Can-Berk/7453eb0068f11138aa3bb3f5a9221e89/translation_audiosynthesis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# ESPnet + Multilingual TTS + Audiosynthesis - mixed

This notebook demonstrates translation along with audio synthesis implementation:

- ESPnet from https://github.com/espnet/espnetMultilingual_Text_to_Speech
- Multilingual translation from https://github.com/Tomiinek/Multilingual_Text_to_Speech






In [ ]:
# OS setup
!cat /etc/os-release
!apt-get install -qq bc tree sox

# espnet and moses setup
!git clone -q https://github.com/ShigekiKarita/espnet.git;
!pip install -q torch==1.1
!cd espnet; git checkout c0466d9a356c1a33f671a546426d7bc33b5b17e8; pip install -q -e .
!cd espnet/tools/; make moses.done

# download pre-compiled warp-ctc and kaldi tools
!espnet/utils/download_from_google_drive.sh \
    "https://drive.google.com/open?id=13Y4tSygc8WtqzvAVGK_vRV9GlV7TRC0w" espnet/tools tar.gz > /dev/null

# make dummy activate
!mkdir -p espnet/tools/venv/bin && touch espnet/tools/venv/bin/activate
!echo "setup done."

!git clone https://github.com/Tomiinek/Multilingual_Text_to_Speech.git;
#!cd Multilingual_Text_to_Speech

NAME="Ubuntu"
VERSION="18.04.5 LTS (Bionic Beaver)"
ID=ubuntu
ID_LIKE=debian
PRETTY_NAME="Ubuntu 18.04.5 LTS"
VERSION_ID="18.04"
HOME_URL="https://www.ubuntu.com/"
SUPPORT_URL="https://help.ubuntu.com/"
BUG_REPORT_URL="https://bugs.launchpad.net/ubuntu/"
PRIVACY_POLICY_URL="https://www.ubuntu.com/legal/terms-and-policies/privacy-policy"
VERSION_CODENAME=bionic
UBUNTU_CODENAME=bionic
Selecting previously unselected package libopencore-amrnb0:amd64.
(Reading database ... 160980 files and directories currently installed.)
Preparing to unpack .../0-libopencore-amrnb0_0.1.3-2.1_amd64.deb ...
Unpacking libopencore-amrnb0:amd64 (0.1.3-2.1) ...
Selecting previously unselected package libopencore-amrwb0:amd64.
Preparing to unpack .../1-libopencore-amrwb0_0.1.3-2.1_amd64.deb ...
Unpacking libopencore-amrwb0:amd64 (0.1.3-2.1) ...
Selecting previously unselected package libmagic-mgc.
Preparing to unpack .../2-libmagic-mgc_1%3a5.32-2ubuntu0.4_amd64.deb ...
Unpacking libmagic-mgc (1:5.32-2ubuntu0.4)

In [ ]:
#We added En-Fr ST translation link to espnet/utils/translate_wav.sh as current one is outdated

In [ ]:
import sys
import os
import IPython
from IPython.display import display, Audio
from scipy.io import wavfile
import IPython.display as display
import yaml
import numpy as np

! pip install -q -U soundfile
! pip install -q -U phonemizer
! pip install -q -U epitran

     |████████████████████████████████| 51kB 2.7MB/s 
     |████████████████████████████████| 194kB 8.6MB/s 
     |████████████████████████████████| 51kB 5.9MB/s 
     |████████████████████████████████| 143kB 4.3MB/s 
     |████████████████████████████████| 71kB 8.1MB/s 
     |████████████████████████████████| 276kB 30.1MB/s 


In [ ]:
#translation data and to get features of target speakers
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
WAV_FILE = "/content/drive/MyDrive/Project_srp/Translation_project/English_Speech_Inputs/en_speech9.wav"

fs, data = wavfile.read(WAV_FILE)
data = data.astype(np.float)

print('original')
display.display(Audio('/content/drive/MyDrive/Project_srp/Translation_project/English_Speech_Inputs/en_speech9.wav', rate=48000))

original


In [ ]:
# downsample to 16 kHz for ST model
os.chdir("/content/espnet/egs/must_c/st1")
!sox '/content/drive/MyDrive/Project_srp/Translation_project/English_Speech_Inputs/en_speech9.wav' -b 16 ../../../test_utils/en_speech9k.wav rate 16k pad 0.1 pad 0 0.1

# make decode config
with open("conf/decode_sample.yaml", "w") as f:
    yaml.dump({
        "batchsize": 0,
        "beam-size": 5,
        "ctc-weight": 0.4,
        "lm-weight": 0.6,
        "maxlenratio": 0.0,
        "minlenratio": 0.0,
        "penalty": 0.0,
    }, f, Dumper=yaml.Dumper)

# let's recognize generated speech
!../../../utils/recog_wav.sh --models librispeech.transformer.v1 \
    --decode_config conf/decode_sample.yaml \
    ../../../test_utils/en_speech9k.wav

--2021-03-30 11:51:59--  https://drive.google.com/uc?export=download&id=1BtQvAnsFvVi-dp_qsaFP7n4A_5cwnlR6
Resolving drive.google.com (drive.google.com)... 74.125.203.138, 74.125.203.102, 74.125.203.101, ...
Connecting to drive.google.com (drive.google.com)|74.125.203.138|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: 'decode/download/librispeech.transformer.v1/iBzS5p..tar.gz'

decode/download/lib     [ <=>                ]   3.27K  --.-KB/s    in 0s      

2021-03-30 11:52:00 (48.5 MB/s) - 'decode/download/librispeech.transformer.v1/iBzS5p..tar.gz' saved [3344]


gzip: stdin: not in gzip format
tar: Child returned status 1
tar: Error is not recoverable: exiting now
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  3344    0  3344    0     0  12911      0 --:--:-- --:--:-- --:--:-- 12911
  % Total    % Received % X

In [ ]:
# move on the recipe directory
os.chdir("/content/espnet/egs/must_c/st1")
!../../../utils/translate_wav.sh --models must_c.transformer.v1.en-fr ../../../test_utils/en_speech9k.wav | tee /content/translated.txt

--2021-03-30 11:52:38--  https://drive.google.com/uc?export=download&id=1sB0rKa7Mg9asoLBoM2lgpb04VgX46L3c
Resolving drive.google.com (drive.google.com)... 74.125.203.101, 74.125.203.139, 74.125.203.102, ...
Connecting to drive.google.com (drive.google.com)|74.125.203.101|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: 'decode/download/must_c.transformer.v1.en-fr/MmNUmc..tar.gz'

decode/download/mus     [ <=>                ]   3.30K  --.-KB/s    in 0s      

2021-03-30 11:52:38 (45.2 MB/s) - 'decode/download/must_c.transformer.v1.en-fr/MmNUmc..tar.gz' saved [3379]


gzip: stdin: not in gzip format
tar: Child returned status 1
tar: Error is not recoverable: exiting now
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  3379    0  3379    0     0  13905      0 --:--:-- --:--:-- --:--:-- 13905
  % Total    % Received %

In [ ]:
#model clone
os.chdir(os.path.expanduser("~"))
    
tacotron_dir = "Multilingual_Text_to_Speech"
if not os.path.exists(tacotron_dir):
  ! git clone https://github.com/Tomiinek/Multilingual_Text_to_Speech; # $tacotron_dir

wavernn_dir = "WaveRNN"
if not os.path.exists(wavernn_dir):
  ! git clone https://github.com/Tomiinek/$wavernn_dir;


#pre-trained models
! mkdir -p checkpoints
os.chdir(os.path.join(os.path.expanduser("~"), "checkpoints"))

tacotron_chpt = "generated_switching.pyt"
if not os.path.exists(os.path.join(os.path.expanduser("~"), "checkpoints", tacotron_chpt)):
  ! curl -O -L "https://github.com/Tomiinek/Multilingual_Text_to_Speech/releases/download/v1.0/$tacotron_chpt" 

wavernn_chpt = "wavernn_weight.pyt"
if not os.path.exists(os.path.join(os.path.expanduser("~"), "checkpoints", wavernn_chpt)):
  ! curl -O -L "https://github.com/Tomiinek/Multilingual_Text_to_Speech/releases/download/v1.0/$wavernn_chpt"     

os.chdir(os.path.expanduser("~"))

Cloning into 'Multilingual_Text_to_Speech'...
remote: Enumerating objects: 10, done.
remote: Counting objects: 100% (10/10), done.
remote: Compressing objects: 100% (10/10), done.
remote: Total 1227 (delta 3), reused 0 (delta 0), pack-reused 1217
Receiving objects: 100% (1227/1227), 43.10 MiB | 24.73 MiB/s, done.
Resolving deltas: 100% (756/756), done.
Cloning into 'WaveRNN'...
remote: Enumerating objects: 981, done.
remote: Total 981 (delta 0), reused 0 (delta 0), pack-reused 981
Receiving objects: 100% (981/981), 242.14 MiB | 25.85 MiB/s, done.
Resolving deltas: 100% (564/564), done.
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100   631  100   631    0     0   1696      0 --:--:-- --:--:-- --:--:--  1696
100  163M  100  163M    0     0  17.2M      0  0:00:09  0:00:09 --:--:-- 20.1M
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
           

### **TTS using ESPnet outputs**

In [ ]:
#From the outputs of E2E-ST (line 6)
inputs = [
    "Le Maroc et moi-même aimons le traitement spécial lorsqu' on exporte l' Europe.|00-fr|fr", #from en_speech1
    "Le secteur audio visuel est très important.|00-fr|fr", #from en_speech2
    "Il y a un lien entre toutes ces découvertes.|00-fr|fr", #from en_speech3
    "Les électrons modernes sont devenus hautement dépendants des chimies inorganiques.|00-fr|fr", #from en_speech4
    "Mais c' est aussi rafraîchissant de lire un auteur japonais.|00-fr|fr", #from en_speech5
    "Le nombre de canaux de télévision dans nos bureaux a augmenté considérablement.|00-fr|fr", #from en_speech6
    "Est-ce que tout le monde est déconcerté, et personne n' a une opinion qui a duré plus de 30 secondes?|00-fr|fr", # from en_speech7
    "Mais y a-t-il des commentaires?|00-fr|fr", #from en_speech8
    "La différence dans l' arc-en-ciel dépend considérablement de la taille des gouttes, et la largeur de la bande colorée augmente alors que la taille de la goutte augmente.|00-fr|fr", #from en_speech9
]

In [ ]:
#Spectrogram generation
os.chdir(os.path.join(os.path.expanduser("~"), tacotron_dir))
if "utils" in sys.modules: del sys.modules["utils"]

from synthesize import synthesize
from utils import build_model

model = build_model(os.path.join(os.path.expanduser("~"), "checkpoints", tacotron_chpt))
model.eval()

spectrograms = [synthesize(model, "|" + i) for i in inputs]

#Waveform generation
os.chdir(os.path.join(os.path.expanduser("~"), wavernn_dir))
if "utils" in sys.modules: del sys.modules["utils"]

from models.fatchord_version import WaveRNN
from utils import hparams as hp
from gen_wavernn import generate
import torch

hp.configure('hparams.py')
model = WaveRNN(rnn_dims=hp.voc_rnn_dims, fc_dims=hp.voc_fc_dims, bits=hp.bits, pad=hp.voc_pad, upsample_factors=hp.voc_upsample_factors, 
                feat_dims=hp.num_mels, compute_dims=hp.voc_compute_dims, res_out_dims=hp.voc_res_out_dims, res_blocks=hp.voc_res_blocks, 
                hop_length=hp.hop_length, sample_rate=hp.sample_rate, mode=hp.voc_mode).to(torch.device('cuda' if torch.cuda.is_available() else 'cpu'))
model.load(os.path.join(os.path.expanduser("~"), "checkpoints", wavernn_chpt))

waveforms = [generate(model, s, hp.voc_gen_batched, hp.voc_target, hp.voc_overlap) for s in spectrograms]

Trainable Parameters: 4.744M
| ████████████████ 204000/205700 | Batch Size: 17 | Gen Rate: 24.0kHz | 

## Resulting audios



In [ ]:
for idx, w in enumerate(waveforms):
  print(inputs[idx])
  IPython.display.display(IPython.display.Audio(data=w, rate=hp.sample_rate))

Le Maroc et moi-même aimons le traitement spécial lorsqu' on exporte l' Europe.|00-fr|fr


Le secteur audio visuel est très important.|00-fr|fr


Il y a un lien entre toutes ces découvertes.|00-fr|fr


Les électrons modernes sont devenus hautement dépendants des chimies inorganiques.|00-fr|fr


Mais c' est aussi rafraîchissant de lire un auteur japonais.|00-fr|fr


Le nombre de canaux de télévision dans nos bureaux a augmenté considérablement.|00-fr|fr


Est-ce que tout le monde est déconcerté, et personne n' a une opinion qui a duré plus de 30 secondes?|00-fr|fr


Mais y a-t-il des commentaires?|00-fr|fr


La différence dans l' arc-en-ciel dépend considérablement de la taille des gouttes, et la largeur de la bande colorée augmente alors que la taille de la goutte augmente.|00-fr|fr


In [ ]:
!pip install torch==1.6.0+cu101 -f https://download.pytorch.org/whl/torch_stable.html
!pip install torchvision==0.7.0+cu101 -f https://download.pytorch.org/whl/torch_stable.html
!pip install numba==0.48
#!pip install 'git+https://github.com/lanpa/tensorboardX'
!pip freeze
!pip install imageio==2.6.1
!pip install imageio-ffmpeg==0.3.0
!pip install numba==0.48
!pip install librosa==0.7.2
!pip install matplotlib==3.0.0
!pip install numpy==1.17.3
!pip install opencv-python==3.4.2.17
!pip install scikit-image==0.14.1
!pip install scikit-learn==0.20.0
!pip install scipy==1.1.0
!pip install sklearn==0.0
!pip install tqdm==4.36.1
!pip install tensorflow-gpu==1.14.0
!pip install tensorflow==1.14.0

Looking in links: https://download.pytorch.org/whl/torch_stable.html
     |████████████████████████████████| 708.0MB 21kB/s 
ERROR: torchvision 0.9.0+cu101 has requirement torch==1.8.0, but you'll have torch 1.6.0+cu101 which is incompatible.
ERROR: torchtext 0.9.0 has requirement torch==1.8.0, but you'll have torch 1.6.0+cu101 which is incompatible.
  Found existing installation: torch 1.1.0
    Uninstalling torch-1.1.0:
      Successfully uninstalled torch-1.1.0


Looking in links: https://download.pytorch.org/whl/torch_stable.html
     |████████████████████████████████| 5.9MB 13.7MB/s 
  Found existing installation: torchvision 0.9.0+cu101
    Uninstalling torchvision-0.9.0+cu101:
      Successfully uninstalled torchvision-0.9.0+cu101
     |████████████████████████████████| 3.6MB 5.7MB/s 
     |████████████████████████████████| 20.2MB 6.4MB/s 
ERROR: umap-learn 0.5.1 has requirement numba>=0.49, but you'll have numba 0.48.0 which is incompatible.
ERROR: pynndescent 0.5.2 has requirement numba>=0.51.2, but you'll have numba 0.48.0 which is incompatible.
  Found existing installation: llvmlite 0.34.0
    Uninstalling llvmlite-0.34.0:
      Successfully uninstalled llvmlite-0.34.0
  Found existing installation: numba 0.51.2
    Uninstalling numba-0.51.2:
      Successfully uninstalled numba-0.51.2


absl-py==0.10.0
alabaster==0.7.12
albumentations==0.1.12
altair==4.1.0
appdirs==1.4.4
argon2-cffi==20.1.0
asgiref==3.3.1
astor==0.8.1
astropy==4.2
astunparse==1.6.3
async-generator==1.10
atari-py==0.2.6
atomicwrites==1.4.0
attrs==20.3.0
audioread==2.1.9
autograd==1.3
Babel==2.9.0
backcall==0.2.0
beautifulsoup4==4.6.3
bleach==3.3.0
blis==0.4.1
bokeh==2.1.1
Bottleneck==1.3.2
branca==0.4.2
bs4==0.0.1
CacheControl==0.12.6
cachetools==4.2.1
catalogue==1.0.0
certifi==2020.12.5
cffi==1.14.5
chainer==6.0.0
chardet==3.0.4
click==7.1.2
clldutils==3.7.0
cloudpickle==1.3.0
cmake==3.12.0
cmdstanpy==0.9.5
colorlog==4.8.0
colorlover==0.3.0
community==1.0.0b1
ConfigArgParse==1.4
contextlib2==0.5.5
convertdate==2.3.1
coverage==3.7.1
coveralls==0.5
crcmod==1.7
csvw==1.10.1
cufflinks==0.17.3
cupy-cuda101==7.4.0
cvxopt==1.2.6
cvxpy==1.0.31
cycler==0.10.0
cymem==2.0.5
Cython==0.29.22
daft==0.0.4
dask==2.12.0
datascience==0.10.6
debugpy==1.0.0
decorator==4.4.2
defusedxml==0.7.1
descartes==1.1.0
dill==0.3.3


     |████████████████████████████████| 12.8MB 3.9MB/s 
ERROR: yellowbrick 0.9.1 has requirement matplotlib!=3.0.0,>=1.5.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: scikit-image 0.16.2 has requirement matplotlib!=3.0.0,>=2.0.0, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: plotnine 0.6.0 has requirement matplotlib>=3.1.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: mizani 0.6.0 has requirement matplotlib>=3.1.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
ERROR: espnet 0.6.1 has requirement matplotlib>=3.1.0, but you'll have matplotlib 3.0.0 which is incompatible.
  Found existing installation: matplotlib 3.2.2
    Uninstalling matplotlib-3.2.2:
      Successfully uninstalled matplotlib-3.2.2


     |████████████████████████████████| 20.0MB 1.4MB/s 
ERROR: yellowbrick 0.9.1 has requirement matplotlib!=3.0.0,>=1.5.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: umap-learn 0.5.1 has requirement numba>=0.49, but you'll have numba 0.48.0 which is incompatible.
ERROR: torchtext 0.9.0 has requirement torch==1.8.0, but you'll have torch 1.6.0+cu101 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement h5py~=2.10.0, but you'll have h5py 2.9.0 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement numpy~=1.19.2, but you'll have numpy 1.17.3 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement protobuf>=3.9.2, but you'll have protobuf 3.7.1 which is incompatible.
ERROR: tensorflow-hub 0.11.0 has requirement protobuf>=3.8.0, but you'll have protobuf 3.7.1 which is incompatible.
ERROR: tensorboardx 2.1 has requirement protobuf>=3.8.0, but you'll have protobuf 3.7.1 which is incompatible.
ERROR: scikit-image 0.16.2 has requirement matplotlib!=3

     |████████████████████████████████| 25.0MB 1.5MB/s 
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: opencv-python 4.1.2.30
    Uninstalling opencv-python-4.1.2.30:
      Successfully uninstalled opencv-python-4.1.2.30
     |████████████████████████████████| 25.3MB 1.5MB/s 
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
  Found existing installation: scikit-image 0.16.2
    Uninstalling scikit-image-0.16.2:
      Successfully uninstalled scikit-image-0.16.2
     |████████████████████████████████| 5.3MB 4.0MB/s 
ERROR: yellowbrick 0.9.1 has requirement matplotlib!=3.0.0,>=1.5.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: umap-learn 0.5.1 has requirement numba>=0.49, but you'll have numba 0.48.0 which is incompatible.
ERROR: umap-learn 0.5.1 has requirement scikit-learn>=0.22, but you'll have s

     |████████████████████████████████| 31.2MB 174kB/s 
ERROR: yellowbrick 0.9.1 has requirement matplotlib!=3.0.0,>=1.5.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: umap-learn 0.5.1 has requirement numba>=0.49, but you'll have numba 0.48.0 which is incompatible.
ERROR: umap-learn 0.5.1 has requirement scikit-learn>=0.22, but you'll have scikit-learn 0.20.0 which is incompatible.
ERROR: pynndescent 0.5.2 has requirement numba>=0.51.2, but you'll have numba 0.48.0 which is incompatible.
ERROR: plotnine 0.6.0 has requirement matplotlib>=3.1.1, but you'll have matplotlib 3.0.0 which is incompatible.
ERROR: plotnine 0.6.0 has requirement scipy>=1.2.0, but you'll have scipy 1.1.0 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
ERROR: espnet 0.6.1 has requirement matplotlib>=3.1.0, but you'll have matplotlib 3.0.0 which is incompatible.
  Found existing installation: scipy 1.3.3

     |████████████████████████████████| 61kB 3.0MB/s 
ERROR: torchtext 0.9.0 has requirement torch==1.8.0, but you'll have torch 1.6.0+cu101 which is incompatible.
ERROR: spacy 2.2.4 has requirement tqdm<5.0.0,>=4.38.0, but you'll have tqdm 4.36.1 which is incompatible.
ERROR: espnet 0.6.1 has requirement matplotlib>=3.1.0, but you'll have matplotlib 3.0.0 which is incompatible.
  Found existing installation: tqdm 4.41.1
    Uninstalling tqdm-4.41.1:
      Successfully uninstalled tqdm-4.41.1


     |████████████████████████████████| 377.1MB 46kB/s 
     |████████████████████████████████| 3.2MB 47.5MB/s 
     |████████████████████████████████| 491kB 46.7MB/s 
     |████████████████████████████████| 51kB 5.9MB/s 
ERROR: tensorflow 2.4.1 has requirement h5py~=2.10.0, but you'll have h5py 2.9.0 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement numpy~=1.19.2, but you'll have numpy 1.17.3 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement protobuf>=3.9.2, but you'll have protobuf 3.7.1 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement tensorboard~=2.4, but you'll have tensorboard 1.14.0 which is incompatible.
ERROR: tensorflow 2.4.1 has requirement tensorflow-estimator<2.5.0,>=2.4.0, but you'll have tensorflow-estimator 1.14.0 which is incompatible.
  Found existing installation: tensorboard 2.4.1
    Uninstalling tensorboard-2.4.1:
      Successfully uninstalled tensorboard-2.4.1
  Found existing installation: tensorflow-estimator 2.4.0
    U

     |████████████████████████████████| 109.3MB 139kB/s 
  Found existing installation: tensorflow 2.4.1
    Uninstalling tensorflow-2.4.1:
      Successfully uninstalled tensorflow-2.4.1


In [ ]:
!python '/content/drive/MyDrive/Project_srp/Audio_synthesis_project/target_test.py' --model '/content/drive/MyDrive/Project_srp/Audio_synthesis_project/target_outputs/Obama_Train_ex2/Obama_train01.pkl' --wav_path '/content/drive/MyDrive/Project_srp/Translation_project/Corresponding_Fr/fr_speech9.wav' --output_file '/content/drive/MyDrive/Project_srp/Translation_project/Target_Speaker_Fr/Obama_fr9.wav'

/usr/local/lib/python3.7/dist-packages/sklearn/externals/joblib/externals/cloudpickle/cloudpickle.py:47: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  import imp
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a fut

In [ ]:
!python '/content/drive/MyDrive/Project_srp/Audio_synthesis_project/target_test.py' --model '/content/drive/MyDrive/Project_srp/Audio_synthesis_project/target_outputs/Oprah_Train_ex2/Oprah_train01.pkl' --wav_path '/content/drive/MyDrive/Project_srp/Translation_project/Corresponding_Fr/fr_speech9.wav' --output_file '/content/drive/MyDrive/Project_srp/Translation_project/Target_Speaker_Fr/Oprah_fr9.wav'

/usr/local/lib/python3.7/dist-packages/sklearn/externals/joblib/externals/cloudpickle/cloudpickle.py:47: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  import imp
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/usr/local/lib/python3.7/dist-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a fut